In [32]:
#importación de paqueterías

#Procesamiento de datos
import pandas as pd
pd.set_option('display.float_format', lambda x: '%.1f' % x)
import numpy as np

#Visualización
import plotly
import plotly.express as px

#PCA, encoding y normalizar datos
from sklearn.preprocessing import StandardScaler, LabelEncoder
from sklearn.decomposition import PCA

In [33]:
def to_lower(df):
  columnsTolower = list(df.select_dtypes(include=['category','object']))
  for feature in columnsTolower:
      try:
          df[feature] = df[feature].str.lower()
      except:
          print('Error parsing '+feature)
  return df

### Lectura y unión de datasets

In [34]:
mutual_art = pd.read_csv('../datasets/clean/clean_mut_art_ver2.csv').drop(columns=['Unnamed: 0'])
artsy = pd.read_csv('../datasets/clean/datosArtsy.csv')

In [35]:
artsy.height = artsy.height.str.split(' ')
artsy.length = artsy.length.str.split(' ')
artsy.height = artsy.height.apply(lambda x: x[0])
artsy.length = artsy.length.apply(lambda x: x[0])

In [36]:
# Transformación de tipo de datos
df = pd.concat([artsy,mutual_art])
df['height'] = df['height'].astype(float)
df['length'] = df['length'].astype(float)
df['price'] = df['price'].astype(float)
df['performance'] = df['performance'].astype(float)
#df['año_venta'] = pd.to_datetime(df['sale_date'],yearfirst=True)
#df['año_venta'] = df['año_venta'].astype(str).str.slice(stop=4)


# Añadir precio por cm2
df = df.assign(precio_cm2 = lambda x: (x['price']/(x['height']*x['length'])))
#Eliminar valores infinitos (Surgen cuando largo o ancho son 0)
df=df[~df.isin([np.inf, -np.inf]).any(1)]
df=to_lower(df)

In [37]:
df.head(5)

title  height  length       art_type  \
0                        caminadora viajera    50.0    52.6      sculpture   
1  i) untitled; ii) untitled; iii) untitled    33.0    24.8  work on paper   
2                                  untitled    56.0    44.0          print   
3                     study for a sculpture    74.5    54.5  work on paper   
4                                  untitled    29.0    56.0      sculpture   

                                         medium_text  date_text  age  \
0                      bronze with gold-brown patina        NaN  NaN   
1  gouache and graphite on paper; watercolor and ...     1960.0 33.0   
2                                              print        NaN  NaN   
3                                             pastel     1970.0 43.0   
4                                pink carrara marble        NaN  NaN   

        house                sale_date   price            author  performance  \
0   sotheby's  1969-12-31 18:00:40.857 45000.0    abigail varela          0.5   
1  christie's  1969-12-31 18:00:44.397  4000.0  agustin cardenas          0.3   
2    artcuria  1969-12-31 18:00:43.271   226.0  agustin cardenas         -0.2   
3    artcuria  1969-12-31 18:00:43.271  1810.0  agustin cardenas          1.4   
4   sotheby's  1969-12-31 18:00:43.059 43750.0  agustin cardenas          0.6   

  source    country fecha  precio_cm2  
0  artsy  venezuela   NaN        17.1  
1  artsy       cuba   NaN         4.9  
2  artsy       cuba   NaN         0.1  
3  artsy       cuba   NaN         0.4  
4  artsy       cuba   NaN        26.9

### Análisis exploratorio de datos

In [38]:
fig = px.box(df, y="price",points="all",title='Boxplot de precios')
fig.show()

#### Sin outliers

In [39]:
# Eliminar outliers
Q1 = df['price'].quantile(0.25)
Q3 = df['price'].quantile(0.75)
IQR = Q3 - Q1
filter = (df['price'] >= Q1 - 1.5 * IQR) & (df['price'] <= Q3 + 1.5 *IQR)
df_sin_outliers = df.loc[filter]

#graficar
fig = px.box(df_sin_outliers, y="price",title='Boxplot de precios (Sin outliers)')
fig.show()

In [40]:
fig = px.box(df, y="age",points="all",title='Antiguedad de las obras')
fig.show()

In [41]:
fig = px.histogram(df, x="date_text",nbins=160,color='source',title='Distribución Fecha de creación')
fig.show()

In [42]:
fig = px.box(df, y="precio_cm2",points="all",title='Boxplot de precios por cm2')
fig.show()

In [43]:
# Eliminar outliers
Q1 = df['precio_cm2'].quantile(0.25)
Q3 = df['precio_cm2'].quantile(0.75)
IQR = Q3 - Q1
filter = (df['precio_cm2'] >= Q1 - 1.5 * IQR) & (df['precio_cm2'] <= Q3 + 1.5 *IQR)
df_sin_outliers = df.loc[filter]

#graficar
fig = px.box(df_sin_outliers, y="precio_cm2",title='Boxplot de precios por cm2 (Sin outliers)')
fig.show()

In [44]:
filter = (df['precio_cm2'] >= Q1 - 1.5 * IQR) & (df['precio_cm2'] >= Q3 + 1.5 *IQR)
df_outliers = df.loc[filter]

Q1 = df_outliers['precio_cm2'].quantile(0.25)
Q3 = df_outliers['precio_cm2'].quantile(0.75)
IQR = Q3 - Q1

filter = (df_outliers['precio_cm2'] >= Q1 - 1.5 * IQR) & (df_outliers['precio_cm2'] <= Q3 + 1.5 *IQR)
df_out_sin_outliers = df_outliers.loc[filter]

fig = px.box(df_out_sin_outliers,x='source', y="precio_cm2",title='Boxplot de precios por cm2 (Sin outliers de los outliers)')
fig.show()

In [45]:
df_autores = df[['price','author']].groupby(['author']).mean().sort_values(by='price',ascending=False).reset_index()
fig = px.bar(df_autores.head(15), x='author', y='price',title='Precio de obra promedio por autor')
fig.show()

In [46]:
df_precio_cm2 = df[['precio_cm2','author']].groupby(['author']).mean().sort_values(by='precio_cm2',ascending=False).reset_index()
df_precio_cm2
fig = px.bar(df_precio_cm2.head(15), x='author', y='precio_cm2',title='Precio promedio del cm2 por autor')
fig.show()

In [47]:
#df_art_type = df[['medium_text','price','performance','precio_cm2']]
#df_art_type = pd.melt(df_art_type,id_vars='medium_text',value_vars=['price','performance','precio_cm2'])

In [48]:
df_art_medium = df[['medium_text','price']].groupby(['medium_text']).mean().sort_values(by='price',
                                                                                ascending=False).reset_index()

In [49]:
fig = px.bar(df_art_medium.head(15).sort_values(by='price'), x='price', y='medium_text',title='Precio promedio por estilo')
fig.show()

In [76]:
'''
df_art_type = df[['art_type','price']].groupby(['art_type']).mean().sort_values(by='price',
                                                                                ascending=False).reset_index()
fig = px.bar(df_art_type.head(15).sort_values(by='price'), x='price', y='art_type',title='Precio promedio por estilo')
fig.show()
'''

"\ndf_art_type = df[['art_type','price']].groupby(['art_type']).mean().sort_values(by='price',\n                                                                                ascending=False).reset_index()\nfig = px.bar(df_art_type.head(15).sort_values(by='price'), x='price', y='art_type',title='Precio promedio por estilo')\nfig.show()\n"

In [81]:
top_obras = df[['title','price']].groupby(['title']).agg({'price':['sum','count','mean','max']})
top_obras = top_obras['price']
top_obras = top_obras.sort_values(by='max',ascending=False).reset_index()

In [82]:
fig = px.bar(top_obras.head(15), x='title', y='max',title='Obras con mayor precio')
fig.show()

In [75]:
fig = px.bar(top_obras.head(15), x='', y='medium_text',title='Precio promedio por estilo')
fig.show()

sum  count  \
title                                                                  
diego y yo                                         35010119.0      2   
dos desnudos en el bosque (la tierra misma)        16010000.0      2   
armonía (autorretrato sugerente)                    6186800.0      1   
perro aullando a la luna (dog howling at the mo...  5873000.0      1   
portrait of a lady in white                         5836500.0      1   
...                                                       ...    ...   
woman standing                                            0.0      0   
woodblock print                                           0.0      0   
zapatería                                                 0.0      0   
zwei tanzende weibliche figuren aus der "karnev...        0.0      0   
“parisino con pipa en el bar”                             0.0      0   

                                                         mean  
title                                                          
diego y yo                                         17505059.5  
dos desnudos en el bosque (la tierra misma)         8005000.0  
armonía (autorretrato sugerente)                    6186800.0  
perro aullando a la luna (dog howling at the mo...  5873000.0  
portrait of a lady in white                         5836500.0  
...                                                       ...  
woman standing                                            NaN  
woodblock print                                           NaN  
zapatería                                                 NaN  
zwei tanzende weibliche figuren aus der "karnev...        NaN  
“parisino con pipa en el bar”                             NaN  

[12015 rows x 3 columns]

In [28]:
corr = df[['height','length','age','price','performance','precio_cm2']].corr()
corr.style.background_gradient (cmap = 'coolwarm')

## Análisis de componentes principales

In [20]:
#Codificacción de variables
def Encoder(df):
  columnsToEncode = list(df.select_dtypes(include=['category','object']))
  le = LabelEncoder()
  for feature in columnsToEncode:
      try:
          df[feature] = le.fit_transform(df[feature])
      except:
          print('Error encoding '+feature)
  return df
data_codificada = Encoder(df)

#Eliminar valores nulos e infinitos
data_codificada=data_codificada[~data_codificada.isin([np.nan, np.inf, -np.inf]).any(1)]
#Cambiar a valores por desviaciones estandar
data_codificada['target'] = data_codificada['performance'].apply(lambda x: 'Alto' if x > 7 else 
                                                                 ('Medio' if x>5 else 
                                                                  ('Regular' if x>3 else 'Bajo')))

/var/folders/c7/yrk77vqj3jj31wf8sfvg8tyw0000gn/T/ipykernel_43326/3220739249.py:16: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [21]:
data_codificada['target'].value_counts()

Bajo       16504
Regular      655
Medio        122
Alto         102
Name: target, dtype: int64

In [22]:
data_codificada.performance.describe()

count   17383.0
mean        1.1
std         1.9
min        -1.0
25%         0.1
50%         0.9
75%         1.6
max       171.6
Name: performance, dtype: float64

In [23]:
data_codificada.shape

(17383, 17)

In [24]:
features = ['height', 'length', 'art_type', 'medium_text', 'date_text',
       'age', 'house', 'sale_date', 'price', 'author', 'performance', 'source',
       'country', 'fecha', 'precio_cm2']
# Separating out the features
x = data_codificada.loc[:, features].values
#Estandarizar los datos
x = StandardScaler().fit_transform(x)
#Variables objetivo
y = data_codificada.loc[:,['target']].values
#PCA
pca = PCA(n_components=2)
principalComponents = pca.fit_transform(x)
principalDf = pd.DataFrame(data = principalComponents
             , columns = ['principal component 1', 'principal component 2'])
targetDf = pd.DataFrame(data = y
             , columns = ['target'])
finalDf = pd.concat([principalDf, targetDf], axis = 1).reset_index()

In [25]:
fig = px.scatter(x=finalDf["principal component 1"], y=finalDf["principal component 2"],color=finalDf['target'])
fig.show()

In [26]:
pca = PCA(n_components=3)
principalComponents = pca.fit_transform(x)
principalDf = pd.DataFrame(data = principalComponents
             , columns = ['principal component 1', 'principal component 2', 'principal component 3'])
targetDf = pd.DataFrame(data = y
             , columns = ['target'])
finalDf = pd.concat([principalDf, targetDf], axis = 1).reset_index()

In [27]:
fig = px.scatter_3d(x=finalDf["principal component 1"], y=finalDf["principal component 2"],z=finalDf['principal component 3'],color=finalDf['target'])
fig.show()